# TP2 &ndash; Chaînes d'octets

Dans ce TP, nous allons cette fois chiffrer des chaînes d'octets.

Première chose à faire : double-cliquer sur ce texte pour inscrire <b style="color: red">vos noms ici</b>.

## 0) Octets

Les objets `bytes` en Python 3 sont essentiellement des listes d'entiers entre 0 et 255 : 

In [ ]:
a = bytes([72, 69, 76, 76, 79])

a

Les caractères ASCII correspondants sont affichés lorsque possible (le `b` nous rappelle qu'il ne s'agit pas d'une chaîne de caractères normale mais d'une liste d'octets), mais les octets individuels ne devraient pas être considérés en tant que « caractères » (leurs valeurs entières sont renvoyées) :

In [ ]:
for c in a:
    print(c)

Aussi, soyons conscients que la plupart des valeurs ne correspondent pas à des caractères ASCII qui vont s'afficher joliment :

In [ ]:
b = bytes([145, 8, 203, 78, 23])
b

Des valeurs hexadécimales sont affichées pour les octets lorsqu'il n'y a pas de meilleure option ; en général, c'est ainsi qu'il vaudra mieux afficher une chaîne d'octets contenant possiblement des valeurs non affichables (2 chiffres hexadécimaux pour chaque octet).

In [ ]:
b.hex()

Il est facile d'implémenter l'opérateur XOR (ou $\oplus$) pour les octets puisque Python dispose d'un opérateur XOR bit à bit pour les entiers.

In [ ]:
def xor(a: bytes, b: bytes):

    return bytes([x^y for x,y in zip(a,b)])

print("a      :", a.hex())
print("b      :", b.hex())
print("a xor b:", xor(a,b).hex())

**À faire :** Avant de continuer, assurez-vous d'avoir bien compris tout ce qui précède (d'expérience, vous devrez probablement revenir le consulter d'ici quelques minutes)...

Pour vous échauffer, assurez-vous que que vous savez transformer une chaîne de caractères représentant un entier en hexadécimal (comme `'48454c4c4f'`) ou une chaîne de caractères imprimables (comme `'HELLO'`) en objet `bytes` (comme `a`).

## 1) Exploiter la malléabilité

L'encodage ASCII est ainsi fait que les lettres minuscules, numérotées consécutivement, diffèrent de leur version majuscule en exactement 1 bit (le troisième). Par exemple :

In [ ]:
bytes([65])  # 01000001

In [ ]:
bytes([97])  # 01100001

ce qui signifie que l'on peut changer la casse d'un caractère (de minuscule vers majuscule ou vice-versa) et effectuant une opération XOR :

In [ ]:
xor( bytes([97]), bytes([32]) )

Supposez que vous avez intercepté le message chiffré `c1` ci-dessous, que vous savez être la version chiffrée par Chacha20 d'un message `m1` (inconnu pour l'instant) qui est une chaîne d'octets formée de caractères imprimables.

In [ ]:
c1 = bytes.fromhex("80ba031248068c")

Sauriez-vous fabriquer une suite d'octets `c2` qui soit la version chiffrée de `m2`, le message `m1` dans lequel la casse de chaque caractère a été modifiée ?

(divulgâchage ci-dessous à ne pas consulter avant d'avoir votre candidat pour `m2` !)


.



.



.



.



.



.



.



.





.



.



.



.



.



.



.



.





.



.



.



.



.



.



.



.



En utilisant l'ingénierie sociale, vous apprenez que le message `m1` était `ItWorks`. Sachant cela :

- en déduire le masque utilisé lors du chiffrement (notez que cela ne nous donne pas directement la connaissance de la clé utilisée) ;
- l'utiliser pour déchiffrer votre message `c2` et vérifier le bon fonctionnement de votre attaque.

## 2) Utilisation d'AES

Nous allons utiliser l'implémentation d'AES fournie par la librairie <a href="https://pypi.org/project/cryptography/">cryptography</a> (`pip install cryptography` au besoin).

In [ ]:
import os

# Hazardous Materials : n'utiliser que dans des applications de la
# vraie vie que si vous savez absolument ce que vous faites !

from cryptography.hazmat.primitives.ciphers import Cipher
from cryptography.hazmat.primitives.ciphers.algorithms import AES
from cryptography.hazmat.primitives.ciphers.modes import ECB
from cryptography.hazmat.backends import default_backend

AES utilise des blocs de 128 bits, _i.e._ 16 octets.

In [ ]:
AES.block_size # in bits

Initialisons donc un cryptosystème AES avec une clé aléatoire de 16 octets. 

In [ ]:
k = os.urandom(16)

print("Clé secrète :", k.hex())

cipher = Cipher(AES(k), ECB(), default_backend())

encryptor = cipher.encryptor()  # E_k = E(k, ) dans le cours

Nous pouvons donc commencer à chiffrer des chaînes d'octets.

In [ ]:
m = b"Don't forget to respect the block length. A reversible padding scheme is needed in general.#####"

encryptor = cipher.encryptor()
c = encryptor.update(m)

for i in range(len(c)//16):
    print(c[16*i:16*(i+1)].hex())

In [ ]:
decryptor = cipher.decryptor()
decryptor.update(c)

Notez ce qui se produit lorsque des blocs se répètent : 

In [ ]:
m = b"Don't use ECB...Don't use ECB...Don't use ECB..."

c = encryptor.update(m)

for i in range(len(c)//16):
    print(c[16*i:16*(i+1)].hex())

Ceci compromet la confidentialité du chiffrement, puisque l'attaquant ne devrait pas être capable de savoir que des blocs se répètent dans le message.

<b>À faire</b> : Chiffrer le même message en utilisant AES en mode CTR « à la main » (c'est-à-dire, **ne pas** utiliser l'API `cryptography` API sauf pour chiffrer des blocs isolés, mettre votre chiffreur en mode ECB comme ci-dessus).

Vérifier que Bob arrive à déchiffrer le message chiffré avec seulement la connaissance de celui-ci et de la clé partagée `k`.

## 3) Mélanges de cartes

Considérons un problème apparemment très différent : celui d'un casino en ligne voulant effectuer, de façon _imprévisible_ (pour les joueurs) mais de façon _reproductible_ (pour le casino) un jeu de cartes virtuel à l'aide d'une clé de mélange à 128 bits (probablement dérivée d'une clé maîtresse à l'aide d'un CSPRNG). Il y a $52! \approx 2^{226}$ façons différentes de mélanger un jeu de cartes, donc la description complète du mélange ne peut pas tenir dans la clé de mélange : il doit en être déduit de façon sécurisée.

Une façon simple d'y arriver serait :

1. Représenter les cartes par des chaînes d'octets de la longueur d'un bloc AES
2. Chiffrer tous ces identifiants de cartes à l'aide de la clé de mélange.
3. Trier lexicographiquement les identifiants chiffrés ainsi obtenus.
4. Déchiffrer cette liste trier de façon à obtenir la liste initiale, mélangée.

<b>À faire</b> : Implémenter cette approcher. Quelle est la première main de 5 cartes obtenue à partir de votre jeu de cartes mélangé ?